_Update: I ended up writing my own version of a Web/App.config transform tool that does what I want: [tpt](https://github.com/smcl/tpt)_

I found myself having to mess around with a lot of Web.config transforms recently, I was using [ctt](https://github.com/giansalex/ctt) to check they worked as expected. I don't really like the tool though - the command line parameters are weird (`PS> ctt s:"Web.config" t:"Web.Production.config" d:"test.config" pw` - that `{switch}:"value"` format instead of `--switch=value` is weird) and I dislike that `destination:` is a mandatory param and that I can't just omit it to cause the transformed output to print to stdout.

The second issue is easy to fix - I can change `ctt` to do what I want by applying the following quick-n-hacky diff:

In [ ]:
diff --git a/source/ConfigTransformationTool/ArgumentsLoader.cs b/source/ConfigTransformationTool/ArgumentsLoader.cs
index 3009413..275dc8d 100644
--- a/source/ConfigTransformationTool/ArgumentsLoader.cs
+++ b/source/ConfigTransformationTool/ArgumentsLoader.cs
@@ -12,9 +12,13 @@ namespace OpenSource.ConfigTransformationTool
         {
             get
             {
+                /*
                 return !string.IsNullOrWhiteSpace(SourceFilePath)
                     && !string.IsNullOrWhiteSpace(TransformFilePath)
                     && !string.IsNullOrWhiteSpace(DestinationFilePath);
+                */
+                return !string.IsNullOrWhiteSpace(SourceFilePath)
+                    && !string.IsNullOrWhiteSpace(TransformFilePath);
             }
         }
 
diff --git a/source/ConfigTransformationTool/TransformationTask.cs b/source/ConfigTransformationTool/TransformationTask.cs
index 2f40aaa..fb84f1f 100644
--- a/source/ConfigTransformationTool/TransformationTask.cs
+++ b/source/ConfigTransformationTool/TransformationTask.cs
@@ -110,12 +110,12 @@ namespace OpenSource.ConfigTransformationTool
         /// <returns>Return true if transformation finish successfully, otherwise false.</returns>
         public bool Execute(string destinationFilePath, bool forceParametersTask = false)
         {
-            if (string.IsNullOrWhiteSpace(destinationFilePath))
-            {
-                throw new ArgumentException("Destination file can't be empty.", "destinationFilePath");
-            }
+            //if (string.IsNullOrWhiteSpace(destinationFilePath))
+            //{
+            //    throw new ArgumentException("Destination file can't be empty.", "destinationFilePath");
+            //}
 
-            _log.WriteLine("Start tranformation to '{0}'.", destinationFilePath);
+            //_log.WriteLine("Start tranformation to '{0}'.", destinationFilePath);
 
             if (string.IsNullOrWhiteSpace(SourceFilePath) || !File.Exists(SourceFilePath))
             {
@@ -180,7 +180,15 @@ namespace OpenSource.ConfigTransformationTool
                     outerXml = outerXml.Replace("&#xD;", "\r").Replace("&#xA;", "\n");
                 }
 
-                File.WriteAllText(destinationFilePath, outerXml, encoding);
+                if (string.IsNullOrEmpty(destinationFilePath))
+                {
+                    Console.Write(outerXml);
+                }
+                else
+                {
+                    File.WriteAllText(destinationFilePath, outerXml, encoding);
+                }
 
                 return result;
             }


I could submit a PR but really I wouldn't mind just writing my own from scratch that does exactly what I want.